In [1]:
# %pwd  #look at the current work dir
%cd ..
%pwd

/home/felix/projects/energy-aware-computing


'/home/felix/projects/energy-aware-computing'

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import hvplot
import hvplot.pandas
import holoviews as hv
from bokeh.models import HoverTool
from src.util import TimestampInfo
from src.new_analysis import *

In [4]:
from pathlib import Path
import pandas as pd
import json

In [15]:
loader = DataLoader("data/dgx3")
experiments = loader.experiments
experiments

{'power-limit': Experiment(power-limit),
 'clock-limit': Experiment(clock-limit)}

In [16]:
cl_experiment = loader.experiments["clock-limit"]
pl_experiment = loader.experiments["power-limit"]
cl_experiment, pl_experiment

(Experiment(clock-limit), Experiment(power-limit))

In [17]:
cl_experiment.benchmarks["resnet"].runs, pl_experiment.benchmarks["resnet"].runs 

({'877MHz,135MHz': BenchmarkRun(877MHz,135MHz),
  '877MHz,502MHz': BenchmarkRun(877MHz,502MHz),
  '877MHz,1005MHz': BenchmarkRun(877MHz,1005MHz),
  '877MHz,1530MHz': BenchmarkRun(877MHz,1530MHz)},
 {'150W': BenchmarkRun(150W),
  '200W': BenchmarkRun(200W),
  '235W': BenchmarkRun(235W),
  '250W': BenchmarkRun(250W),
  '300W': BenchmarkRun(300W)})

In [18]:
run = cl_experiment.benchmarks["resnet"].runs["877MHz,1530MHz"]

In [19]:
mean = run.aggregate("hd", "mean")
std = run.aggregate("hd", "std")
low = mean - std
high = mean +std

(hv.Area((mean.data.timestamp, high.data.energy,mean.data.energy),vdims=['y', 'y2']).opts(color= "blue") *
hv.Area((mean.data.timestamp, low.data.energy,mean.data.energy),vdims=['y', 'y2']).opts(color="blue"))

:Overlay
   .Area.I  :Area   [x]   (y,y2)
   .Area.II :Area   [x]   (y,y2)

In [20]:
w150 = pl_experiment.benchmarks["resnet"]
means = w150.get_total_values(aggregate=np.mean)

In [21]:
(-((means - means.iloc[4]) ).set_index("timestamp").energy).hvplot()
#means.iloc[4])

:Curve   [timestamp]   (energy)

In [24]:
experiments["power-limit"].benchmarks["resnet"].boxplot("energy")
#boxplot = df.hvplot.box(y='energy', by='run', height=450, width=800, legend=True)
#boxplot

:BoxWhisker   [run]   (energy)

In [26]:
(experiments["power-limit"].benchmarks["resnet"]
     .plot(metric="edp",data_slice="mean")
     .opts(width=800, height=450,legend_position='bottom_right')
    #, legend_offset=(10, 50))
)

:Overlay
   .Curve.A_150W :Curve   [timestamp]   (edp)
   .Curve.A_200W :Curve   [timestamp]   (edp)
   .Curve.A_235W :Curve   [timestamp]   (edp)
   .Curve.A_250W :Curve   [timestamp]   (edp)
   .Curve.A_300W :Curve   [timestamp]   (edp)

In [92]:
b = experiments["power-limit"].benchmarks["resnet"]
(b
 .plot(metric="clock-gpu",data_slice="mean", data_source="sd")
 .opts(width=800, height=450,legend_position='bottom_right')
    #, legend_offset=(10, 50))
)

:Overlay
   .Curve.A_150W :Curve   [timestamp]   (clock-gpu)
   .Curve.A_200W :Curve   [timestamp]   (clock-gpu)
   .Curve.A_235W :Curve   [timestamp]   (clock-gpu)
   .Curve.A_250W :Curve   [timestamp]   (clock-gpu)
   .Curve.A_300W :Curve   [timestamp]   (clock-gpu)

In [93]:
b.runs["150W"].aggregate("sd", "mean").data["clock-gpu"].mean()

1435.7822380012838

In [94]:
(b
 .plot_raw_power(data_slice="mean")
 .opts(width=800, height=300,legend_position='bottom_right')
     #, legend_offset=(10, 50))
)

:Overlay
   .Curve.A_150W :Curve   [timestamp]   (power)
   .Curve.A_200W :Curve   [timestamp]   (power)
   .Curve.A_235W :Curve   [timestamp]   (power)
   .Curve.A_250W :Curve   [timestamp]   (power)
   .Curve.A_300W :Curve   [timestamp]   (power)

In [35]:
(experiments["clock-limit"].benchmarks["resnet"]
     .plot(metric="energy",data_slice="mean")
     .opts(width=800, height=450,legend_position='bottom_right')
    #, legend_offset=(10, 50))
)

:Overlay
   .Curve.A_877MHz_comma_135MHz  :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_502MHz  :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_1005MHz :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_1530MHz :Curve   [timestamp]   (energy)

In [36]:
(experiments["clock-limit"].benchmarks["resnet"]
     .plot_raw_power(data_slice="mean")
     .opts(width=800, height=300,legend_position='bottom_right')
     #, legend_offset=(10, 50))
)

:Overlay
   .Curve.A_877MHz_comma_135MHz  :Curve   [timestamp]   (power)
   .Curve.A_877MHz_comma_502MHz  :Curve   [timestamp]   (power)
   .Curve.A_877MHz_comma_1005MHz :Curve   [timestamp]   (power)
   .Curve.A_877MHz_comma_1530MHz :Curve   [timestamp]   (power)

In [30]:
(experiments["power-limit"].benchmarks["resnet"]
     .plot_energy(data_slice=3)
     .opts(width=800, height=300,legend_position='bottom_right')
     #, legend_offset=(10, 50))
)*(experiments["clock-limit"].benchmarks["resnet"]
     .plot_energy(data_slice=3)
     .opts(width=800, height=300,legend_position='bottom_right')
  )

:Overlay
   .Curve.A_150W                 :Curve   [timestamp]   (energy)
   .Curve.A_200W                 :Curve   [timestamp]   (energy)
   .Curve.A_235W                 :Curve   [timestamp]   (energy)
   .Curve.A_250W                 :Curve   [timestamp]   (energy)
   .Curve.A_300W                 :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_135MHz  :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_502MHz  :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_1005MHz :Curve   [timestamp]   (energy)
   .Curve.A_877MHz_comma_1530MHz :Curve   [timestamp]   (energy)

In [ ]:
w150 = e3.benchmarks["mnist"].runs["150W"]#.repetitions[0]

In [ ]:
for epoch in w150.timestamps.epochs:
    print(epoch)
    hv.VLine(epoch.begin)

w150.power_hd["energy"] = get_energy(w150.power_hd.power, w150.power_hd.timestamp)

In [ ]:
plots = []
for key, run in experiment.benchmarks["resnet"].runs.items():
    plot = run[0].power_hd.set_index("timestamp").energy.hvplot(label=key)
    plots.append(plot)
    #for epoch in run.timestamps.epochs:
    
    #    plot *= hv.VLine((epoch.begin-run.start_index)/np.timedelta64(1, 's'))
#     if plots is None:
#         plots = plot
#     else:
#         plots *= plot
overlay_plots(plots)

In [ ]:
batches = run.timestamps.timestamps[run.timestamps.timestamps["event"] == "batch_begin"].groupby("data").apply(lambda df: df.reset_index(drop=True)).swaplevel(0,1).loc[0]
batches["timestamp"] = (batches["timestamp"] -run.start_index)/np.timedelta64(1, 's')
batches

In [ ]:
plots = None
for key, run in experiment.benchmarks["resnet"].runs.items():
    plot = run.power_hd.set_index("timestamp").power.hvplot(label=key)
    for epoch in run.timestamps.epochs:
        plot *= hv.VLine(run.normalize_timestamp(epoch.begin))
    #plot *= hv.VLine(run.normalize_timestamp(run.timestamps.experiment_begin))
    #for batch in batches.itertuples():
    #    plot *= hv.VLine(batch.timestamp)
    if plots is None:
        plots = plot
    else:
        plots *= plot
plots